# Kernel Ridge Regression

_Ridge Regression_ (also called _Tikhonov regularization_) is a regualized version of Linear Regression: a _regularization term_ equal to $\alpha \sum_{i=1}^n \theta_i^2$ is added to the cost function. This forces the learning algorithm to not only fit the data but also keep the model weights as small as posible.
The hyperparameter $\alpha$ controls how much you want to refgularize the model. If $\alpha = 0$ then Ridge Regression is just a Linear Regression. If $\alpha$ is very large, then all weights end up very close to zero and the result is flat line going through the data's mean.

$$J(\theta) = MSE(\theta) + \alpha \frac{1}{2}\sum_{i=0}^n \theta_i^2$$


It is important to scale the data before performing Ridge Regression, as it is sensitive to the scale of the input features. This is true of most regularized models.

## Preparación de ambiente

In [1]:
from sklearn.model_selection import cross_val_score, train_test_split, RandomizedSearchCV, GridSearchCV
from sklearn.preprocessing import MinMaxScaler
from sklearn.kernel_ridge import KernelRidge
from sklearn.datasets import fetch_openml
from sklearn.linear_model import Ridge
from sklearn.metrics import r2_score
import pandas as pd
import numpy as np

pd.set_option("display.max_columns", 100)

## Load data

In [2]:
housing = fetch_openml(name="house_prices", as_frame=True)

In [3]:
housing

{'data':         Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
 0        1          60       RL         65.0     8450   Pave   NaN      Reg   
 1        2          20       RL         80.0     9600   Pave   NaN      Reg   
 2        3          60       RL         68.0    11250   Pave   NaN      IR1   
 3        4          70       RL         60.0     9550   Pave   NaN      IR1   
 4        5          60       RL         84.0    14260   Pave   NaN      IR1   
 ...    ...         ...      ...          ...      ...    ...   ...      ...   
 1455  1456          60       RL         62.0     7917   Pave   NaN      Reg   
 1456  1457          20       RL         85.0    13175   Pave   NaN      Reg   
 1457  1458          70       RL         66.0     9042   Pave   NaN      Reg   
 1458  1459          20       RL         68.0     9717   Pave   NaN      Reg   
 1459  1460          20       RL         75.0     9937   Pave   NaN      Reg   
 
      LandContour Utilities Lo

In [4]:
housing.keys()

dict_keys(['data', 'target', 'frame', 'categories', 'feature_names', 'target_names', 'DESCR', 'details', 'url'])

In [5]:
housing['DESCR']

"Ask a home buyer to describe their dream house, and they probably won't begin with the height of the basement ceiling or the proximity to an east-west railroad. But this playground competition's dataset proves that much more influences price negotiations than the number of bedrooms or a white-picket fence.\n\nWith 79 explanatory variables describing (almost) every aspect of residential homes in Ames, Iowa, this competition challenges you to predict the final price of each home.\n\nMSSubClass: Identifies the type of dwelling involved in the sale.\t\n\n        20\t1-STORY 1946 & NEWER ALL STYLES\n        30\t1-STORY 1945 & OLDER\n        40\t1-STORY W/FINISHED ATTIC ALL AGES\n        45\t1-1/2 STORY - UNFINISHED ALL AGES\n        50\t1-1/2 STORY FINISHED ALL AGES\n        60\t2-STORY 1946 & NEWER\n        70\t2-STORY 1945 & OLDER\n        75\t2-1/2 STORY ALL AGES\n        80\tSPLIT OR MULTI-LEVEL\n        85\tSPLIT FOYER\n        90\tDUPLEX - ALL STYLES AND AGES\n       120\t1-STORY PUD

In [6]:
df = pd.DataFrame(data = housing["data"], columns=housing["feature_names"])
df["target"] = housing["target"]
tgt = "target"
ls_features = ['MSSubClass', 'LotArea', 'OverallQual', 'OverallCond',
       'YearBuilt', 'YearRemodAdd', 'BsmtFinSF1', 'BsmtFinSF2', 'BsmtUnfSF',
       'TotalBsmtSF', '1stFlrSF', '2ndFlrSF', 'LowQualFinSF', 'GrLivArea',
       'BsmtFullBath', 'BsmtHalfBath', 'FullBath', 'HalfBath', 'BedroomAbvGr',
       'KitchenAbvGr', 'TotRmsAbvGrd', 'Fireplaces', 'GarageCars',
       'GarageArea', 'WoodDeckSF', 'OpenPorchSF', 'EnclosedPorch', '3SsnPorch',
       'ScreenPorch', 'PoolArea', 'MiscVal', 'MoSold', 'YrSold']

In [7]:
df.head()

Id  MSSubClass MSZoning  LotFrontage  LotArea Street Alley LotShape  \
0   1          60       RL         65.0     8450   Pave   NaN      Reg   
1   2          20       RL         80.0     9600   Pave   NaN      Reg   
2   3          60       RL         68.0    11250   Pave   NaN      IR1   
3   4          70       RL         60.0     9550   Pave   NaN      IR1   
4   5          60       RL         84.0    14260   Pave   NaN      IR1   

  LandContour Utilities LotConfig LandSlope Neighborhood Condition1  \
0         Lvl    AllPub    Inside       Gtl      CollgCr       Norm   
1         Lvl    AllPub       FR2       Gtl      Veenker      Feedr   
2         Lvl    AllPub    Inside       Gtl      CollgCr       Norm   
3         Lvl    AllPub    Corner       Gtl      Crawfor       Norm   
4         Lvl    AllPub       FR2       Gtl      NoRidge       Norm   

  Condition2 BldgType HouseStyle  OverallQual  OverallCond  YearBuilt  \
0       Norm     1Fam     2Story            7            5       2003   
1       Norm     1Fam     1Story            6            8       1976   
2       Norm     1Fam     2Story            7            5       2001   
3       Norm     1Fam     2Story            7            5       1915   
4       Norm     1Fam     2Story            8            5       2000   

   YearRemodAdd RoofStyle RoofMatl Exterior1st Exterior2nd MasVnrType  \
0          2003     Gable  CompShg     VinylSd     VinylSd    BrkFace   
1          1976     Gable  CompShg     MetalSd     MetalSd       None   
2          2002     Gable  CompShg     VinylSd     VinylSd    BrkFace   
3          1970     Gable  CompShg   'Wd Sdng'   'Wd Shng'       None   
4          2000     Gable  CompShg     VinylSd     VinylSd    BrkFace   

   MasVnrArea ExterQual ExterCond Foundation BsmtQual BsmtCond BsmtExposure  \
0       196.0        Gd        TA      PConc       Gd       TA           No   
1         0.0        TA        TA     CBlock       Gd       TA           Gd   
2       162.0        Gd        TA      PConc       Gd       TA           Mn   
3         0.0        TA        TA     BrkTil       TA       Gd           No   
4       350.0        Gd        TA      PConc       Gd       TA           Av   

  BsmtFinType1  BsmtFinSF1 BsmtFinType2  BsmtFinSF2  BsmtUnfSF  TotalBsmtSF  \
0          GLQ         706          Unf           0        150          856   
1          ALQ         978          Unf           0        284         1262   
2          GLQ         486          Unf           0        434          920   
3          ALQ         216          Unf           0        540          756   
4          GLQ         655          Unf           0        490         1145   

  Heating HeatingQC CentralAir Electrical  1stFlrSF  2ndFlrSF  LowQualFinSF  \
0    GasA        Ex          Y      SBrkr       856       854             0   
1    GasA        Ex          Y      SBrkr      1262         0             0   
2    GasA        Ex          Y      SBrkr       920       866             0   
3    GasA        Gd          Y      SBrkr       961       756             0   
4    GasA        Ex          Y      SBrkr      1145      1053             0   

   GrLivArea  BsmtFullBath  BsmtHalfBath  FullBath  HalfBath  BedroomAbvGr  \
0       1710             1             0         2         1             3   
1       1262             0             1         2         0             3   
2       1786             1             0         2         1             3   
3       1717             1             0         1         0             3   
4       2198             1             0         2         1             4   

   KitchenAbvGr KitchenQual  TotRmsAbvGrd Functional  Fireplaces FireplaceQu  \
0             1          Gd             8        Typ           0         NaN   
1             1          TA             6        Typ           1          TA   
2             1          Gd             6        Typ           1          TA   
3             1          Gd            

In [8]:
df.describe()

Id   MSSubClass  LotFrontage        LotArea  OverallQual  \
count  1460.000000  1460.000000  1201.000000    1460.000000  1460.000000   
mean    730.500000    56.897260    70.049958   10516.828082     6.099315   
std     421.610009    42.300571    24.284752    9981.264932     1.382997   
min       1.000000    20.000000    21.000000    1300.000000     1.000000   
25%     365.750000    20.000000    59.000000    7553.500000     5.000000   
50%     730.500000    50.000000    69.000000    9478.500000     6.000000   
75%    1095.250000    70.000000    80.000000   11601.500000     7.000000   
max    1460.000000   190.000000   313.000000  215245.000000    10.000000   

       OverallCond    YearBuilt  YearRemodAdd   MasVnrArea   BsmtFinSF1  \
count  1460.000000  1460.000000   1460.000000  1452.000000  1460.000000   
mean      5.575342  1971.267808   1984.865753   103.685262   443.639726   
std       1.112799    30.202904     20.645407   181.066207   456.098091   
min       1.000000  1872.000000   1950.000000     0.000000     0.000000   
25%       5.000000  1954.000000   1967.000000     0.000000     0.000000   
50%       5.000000  1973.000000   1994.000000     0.000000   383.500000   
75%       6.000000  2000.000000   2004.000000   166.000000   712.250000   
max       9.000000  2010.000000   2010.000000  1600.000000  5644.000000   

        BsmtFinSF2    BsmtUnfSF  TotalBsmtSF     1stFlrSF     2ndFlrSF  \
count  1460.000000  1460.000000  1460.000000  1460.000000  1460.000000   
mean     46.549315   567.240411  1057.429452  1162.626712   346.992466   
std     161.319273   441.866955   438.705324   386.587738   436.528436   
min       0.000000     0.000000     0.000000   334.000000     0.000000   
25%       0.000000   223.000000   795.750000   882.000000     0.000000   
50%       0.000000   477.500000   991.500000  1087.000000     0.000000   
75%       0.000000   808.000000  1298.250000  1391.250000   728.000000   
max    1474.000000  2336.000000  6110.000000  4692.000000  2065.000000   

       LowQualFinSF    GrLivArea  BsmtFullBath  BsmtHalfBath     FullBath  \
count   1460.000000  1460.000000   1460.000000   1460.000000  1460.000000   
mean       5.844521  1515.463699      0.425342      0.057534     1.565068   
std       48.623081   525.480383      0.518911      0.238753     0.550916   
min        0.000000   334.000000      0.000000      0.000000     0.000000   
25%        0.000000  1129.500000      0.000000      0.000000     1.000000   
50%        0.000000  1464.000000      0.000000      0.000000     2.000000   
75%        0.000000  1776.750000      1.000000      0.000000     2.000000   
max      572.000000  5642.000000      3.000000      2.000000     3.000000   

          HalfBath  BedroomAbvGr  KitchenAbvGr  TotRmsAbvGrd   Fireplaces  \
count  1460.000000   1460.000000   1460.000000   1460.000000  1460.000000   
mean      0.382877      2.866438      1.046575      6.517808     0.613014   
std       0.502885      0.815778      0.220338      1.625393     0.644666   
min       0.000000      0.000000      0.000000      2.000000     0.000000   
25%       0.000000      2.000000      1.000000      5.000000     0.000000   
50%       0.000000      3.000000      1.000000      6.000000     1.000000   
75%       1.000000      3.000000      1.000000      7.000000     1.000000   
max       2.000000      8.000000      3.000000     14.000000     3.000000   

       GarageYrBlt   GarageCars   GarageArea   WoodDeckSF  OpenPorchSF  \
count  1379.000000  1460.000000  1460.000000  1460.000000  1460.000000   
mean   1978.506164     1.767123   472.980137    94.244521    46.660274   
std      24.689725     0.747315   213.804841   125.338794    66.256028   
min    1900.000000     0.000000     0.000000     0.000000     0.000000   
25%    1961.000000     1.000000   334.500000     0.000000     0.000000   
50%    1980.000000     2.000000   480.000000     0.000000    25.000000   
75%    2002.000000     2.000000   576.000000   168.000000    68.000000   
max    2

In [9]:
df.dropna(axis=1,inplace=True)

In [10]:
df.shape

(1460, 62)

In [11]:
df.head()

Id  MSSubClass MSZoning  LotArea Street LotShape LandContour Utilities  \
0   1          60       RL     8450   Pave      Reg         Lvl    AllPub   
1   2          20       RL     9600   Pave      Reg         Lvl    AllPub   
2   3          60       RL    11250   Pave      IR1         Lvl    AllPub   
3   4          70       RL     9550   Pave      IR1         Lvl    AllPub   
4   5          60       RL    14260   Pave      IR1         Lvl    AllPub   

  LotConfig LandSlope Neighborhood Condition1 Condition2 BldgType HouseStyle  \
0    Inside       Gtl      CollgCr       Norm       Norm     1Fam     2Story   
1       FR2       Gtl      Veenker      Feedr       Norm     1Fam     1Story   
2    Inside       Gtl      CollgCr       Norm       Norm     1Fam     2Story   
3    Corner       Gtl      Crawfor       Norm       Norm     1Fam     2Story   
4       FR2       Gtl      NoRidge       Norm       Norm     1Fam     2Story   

   OverallQual  OverallCond  YearBuilt  YearRemodAdd RoofStyle RoofMatl  \
0            7            5       2003          2003     Gable  CompShg   
1            6            8       1976          1976     Gable  CompShg   
2            7            5       2001          2002     Gable  CompShg   
3            7            5       1915          1970     Gable  CompShg   
4            8            5       2000          2000     Gable  CompShg   

  Exterior1st Exterior2nd ExterQual ExterCond Foundation  BsmtFinSF1  \
0     VinylSd     VinylSd        Gd        TA      PConc         706   
1     MetalSd     MetalSd        TA        TA     CBlock         978   
2     VinylSd     VinylSd        Gd        TA      PConc         486   
3   'Wd Sdng'   'Wd Shng'        TA        TA     BrkTil         216   
4     VinylSd     VinylSd        Gd        TA      PConc         655   

   BsmtFinSF2  BsmtUnfSF  TotalBsmtSF Heating HeatingQC CentralAir  1stFlrSF  \
0           0        150          856    GasA        Ex          Y       856   
1           0        284         1262    GasA        Ex          Y      1262   
2           0        434          920    GasA        Ex          Y       920   
3           0        540          756    GasA        Gd          Y       961   
4           0        490         1145    GasA        Ex          Y      1145   

   2ndFlrSF  LowQualFinSF  GrLivArea  BsmtFullBath  BsmtHalfBath  FullBath  \
0       854             0       1710             1             0         2   
1         0             0       1262             0             1         2   
2       866             0       1786             1             0         2   
3       756             0       1717             1             0         1   
4      1053             0       2198             1             0         2   

   HalfBath  BedroomAbvGr  KitchenAbvGr KitchenQual  TotRmsAbvGrd Functional  \
0         1             3             1          Gd             8        Typ   
1         0             3             1          TA             6        Typ   
2         1             3             1          Gd             6        Typ   
3         0             3             1          Gd             7        Typ   
4         1             4             1          Gd             9        Typ   

   Fireplaces  GarageCars  GarageArea PavedDrive  WoodDeckSF  OpenPorchSF  \
0           0           2         548          Y           0           61   
1           1           2         460          Y         298            0   
2           1           2         608          Y           0           42   
3           1           3         642          Y           0           35   
4           1           3         836          Y         192           84   

   EnclosedPorch  3SsnPorch  ScreenPorch  PoolArea  MiscVal  MoSold  YrSold  \
0              0          0            0         0        0       2    2008   
1              0          0            0         0        0       5    2007   
2              0          0            0    

In [12]:
df.describe()

Id   MSSubClass        LotArea  OverallQual  OverallCond  \
count  1460.000000  1460.000000    1460.000000  1460.000000  1460.000000   
mean    730.500000    56.897260   10516.828082     6.099315     5.575342   
std     421.610009    42.300571    9981.264932     1.382997     1.112799   
min       1.000000    20.000000    1300.000000     1.000000     1.000000   
25%     365.750000    20.000000    7553.500000     5.000000     5.000000   
50%     730.500000    50.000000    9478.500000     6.000000     5.000000   
75%    1095.250000    70.000000   11601.500000     7.000000     6.000000   
max    1460.000000   190.000000  215245.000000    10.000000     9.000000   

         YearBuilt  YearRemodAdd   BsmtFinSF1   BsmtFinSF2    BsmtUnfSF  \
count  1460.000000   1460.000000  1460.000000  1460.000000  1460.000000   
mean   1971.267808   1984.865753   443.639726    46.549315   567.240411   
std      30.202904     20.645407   456.098091   161.319273   441.866955   
min    1872.000000   1950.000000     0.000000     0.000000     0.000000   
25%    1954.000000   1967.000000     0.000000     0.000000   223.000000   
50%    1973.000000   1994.000000   383.500000     0.000000   477.500000   
75%    2000.000000   2004.000000   712.250000     0.000000   808.000000   
max    2010.000000   2010.000000  5644.000000  1474.000000  2336.000000   

       TotalBsmtSF     1stFlrSF     2ndFlrSF  LowQualFinSF    GrLivArea  \
count  1460.000000  1460.000000  1460.000000   1460.000000  1460.000000   
mean   1057.429452  1162.626712   346.992466      5.844521  1515.463699   
std     438.705324   386.587738   436.528436     48.623081   525.480383   
min       0.000000   334.000000     0.000000      0.000000   334.000000   
25%     795.750000   882.000000     0.000000      0.000000  1129.500000   
50%     991.500000  1087.000000     0.000000      0.000000  1464.000000   
75%    1298.250000  1391.250000   728.000000      0.000000  1776.750000   
max    6110.000000  4692.000000  2065.000000    572.000000  5642.000000   

       BsmtFullBath  BsmtHalfBath     FullBath     HalfBath  BedroomAbvGr  \
count   1460.000000   1460.000000  1460.000000  1460.000000   1460.000000   
mean       0.425342      0.057534     1.565068     0.382877      2.866438   
std        0.518911      0.238753     0.550916     0.502885      0.815778   
min        0.000000      0.000000     0.000000     0.000000      0.000000   
25%        0.000000      0.000000     1.000000     0.000000      2.000000   
50%        0.000000      0.000000     2.000000     0.000000      3.000000   
75%        1.000000      0.000000     2.000000     1.000000      3.000000   
max        3.000000      2.000000     3.000000     2.000000      8.000000   

       KitchenAbvGr  TotRmsAbvGrd   Fireplaces   GarageCars   GarageArea  \
count   1460.000000   1460.000000  1460.000000  1460.000000  1460.000000   
mean       1.046575      6.517808     0.613014     1.767123   472.980137   
std        0.220338      1.625393     0.644666     0.747315   213.804841   
min        0.000000      2.000000     0.000000     0.000000     0.000000   
25%        1.000000      5.000000     0.000000     1.000000   334.500000   
50%        1.000000      6.000000     1.000000     2.000000   480.000000   
75%        1.000000      7.000000     1.000000     2.000000   576.000000   
max        3.000000     14.000000     3.000000     4.000000  1418.000000   

        WoodDeckSF  OpenPorchSF  EnclosedPorch    3SsnPorch  ScreenPorch  \
count  1460.000000  1460.000000    1460.000000  1460.000000  1460.000000   
mean     94.244521    46.660274      21.954110     3.409589    15.060959   
std     125.338794    66.256028      61.119149    29.317331    55.757415   
min       0.000000     0.000000       0.000000     0.000000     0.000000   
25%       0.000000     0.000000       0.000000     0.000000     0.000000   
50%       0.000000    25.000000       0.000000     0.000000     0.000000   
75%     168.000000    68.000000       0.000000     0.000000     0.00

In [13]:
df.shape

(1460, 62)

## Data preparation

In [14]:
X = df[ls_features]
y = df[[tgt]]

In [15]:
X_train, X_test, y_train, y_test = train_test_split(X, y, train_size = 0.7)

In [16]:
mm_x = MinMaxScaler()
mm_y = MinMaxScaler()

In [17]:
Xs = mm_x.fit_transform(X_train) 
ys = mm_y.fit_transform(y_train)

## Model

### Ridge Regression

In [18]:
param_grid = {
    "alpha": [x/1000 for x in range(300)] + [x for x in range(100)],
    "tol": [0.00001, 0.0000001, 0.01],
    "solver": ['auto', 'svd', 'cholesky', 'lsqr', 'sparse_cg', 'sag', 'saga']
}

In [19]:
n_hyper = np.prod([x for x in map(len, param_grid.values())])

In [20]:
n_hyper

np.int64(8400)

In [21]:
%%time
model = Ridge()
model.fit(Xs, ys)
clf = GridSearchCV(model, param_grid, cv=4, error_score=-1000, n_jobs=-1, scoring="r2", verbose=4)
clf.fit(Xs, ys)
print("Best score: " + str(clf.best_score_))
print("Best estimator: " + str(clf.best_estimator_))

Fitting 4 folds for each of 8400 candidates, totalling 33600 fits


/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=1.90136e-18): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=1.90136e-18): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=1.90136e-18): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=1.90136e-18): result may not be acc

[CV 1/4] END ..alpha=0.0, solver=auto, tol=0.01;, score=0.851 total time=   0.0s
[CV 3/4] END ..alpha=0.0, solver=saga, tol=0.01;, score=0.810 total time=   0.0s
[CV 4/4] END ..alpha=0.0, solver=saga, tol=0.01;, score=0.407 total time=   0.0s
[CV 1/4] END alpha=0.001, solver=auto, tol=1e-07;, score=0.851 total time=   0.0s
[CV 2/4] END alpha=0.001, solver=auto, tol=1e-07;, score=0.725 total time=   0.0s
[CV 1/4] END .alpha=0.001, solver=svd, tol=0.01;, score=0.851 total time=   0.0s
[CV 2/4] END .alpha=0.001, solver=svd, tol=0.01;, score=0.725 total time=   0.0s
[CV 1/4] END alpha=0.001, solver=lsqr, tol=1e-05;, score=0.851 total time=   0.0s
[CV 2/4] END alpha=0.001, solver=lsqr, tol=1e-05;, score=0.725 total time=   0.0s
[CV 3/4] END alpha=0.001, solver=lsqr, tol=1e-05;, score=0.807 total time=   0.0s
[CV 4/4] END alpha=0.001, solver=lsqr, tol=1e-05;, score=0.404 total time=   0.0s
[CV 1/4] END alpha=0.001, solver=saga, tol=1e-05;, score=0.851 total time=   0.0s
[CV 2/4] END alpha=0.

/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:349: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV 4/4] END .alpha=0.0, solver=auto, tol=1e-05;, score=0.405 total time=   0.0s
[CV 3/4] END ...alpha=0.0, solver=svd, tol=0.01;, score=0.773 total time=   0.0s
[CV 1/4] END alpha=0.0, solver=cholesky, tol=1e-05;, score=0.851 total time=   0.0s
[CV 3/4] END alpha=0.0, solver=cholesky, tol=1e-05;, score=0.807 total time=   0.0s
[CV 1/4] END alpha=0.0, solver=cholesky, tol=1e-07;, score=0.851 total time=   0.0s
[CV 3/4] END alpha=0.0, solver=cholesky, tol=1e-07;, score=0.807 total time=   0.0s
[CV 1/4] END alpha=0.0, solver=cholesky, tol=0.01;, score=0.851 total time=   0.0s
[CV 2/4] END .alpha=0.0, solver=lsqr, tol=1e-05;, score=0.725 total time=   0.0s
[CV 2/4] END .alpha=0.0, solver=lsqr, tol=1e-07;, score=0.725 total time=   0.0s
[CV 1/4] END ..alpha=0.0, solver=lsqr, tol=0.01;, score=0.846 total time=   0.0s
[CV 2/4] END ..alpha=0.0, solver=lsqr, tol=0.01;, score=0.743 total time=   0.0s
[CV 1/4] END alpha=0.0, solver=sparse_cg, tol=1e-05;, score=0.851 total time=   0.0s
[CV 1/4] E

...

[CV 1/4] END alpha=0.294, solver=svd, tol=1e-05;, score=0.852 total time=   0.0s
[CV 2/4] END alpha=0.294, solver=svd, tol=1e-05;, score=0.742 total time=   0.0s
[CV 3/4] END alpha=0.294, solver=svd, tol=1e-05;, score=0.808 total time=   0.0s
[CV 4/4] END alpha=0.294, solver=svd, tol=1e-05;, score=0.441 total time=   0.0s
[CV 1/4] END alpha=0.294, solver=svd, tol=1e-07;, score=0.852 total time=   0.0s
[CV 2/4] END alpha=0.294, solver=svd, tol=1e-07;, score=0.742 total time=   0.0s
[CV 3/4] END alpha=0.294, solver=svd, tol=1e-07;, score=0.808 total time=   0.0s
[CV 4/4] END alpha=0.294, solver=svd, tol=1e-07;, score=0.441 total time=   0.0s
[CV 1/4] END .alpha=0.294, solver=svd, tol=0.01;, score=0.852 total time=   0.0s
[CV 2/4] END .alpha=0.294, solver=svd, tol=0.01;, score=0.742 total time=   0.0s
[CV 3/4] END .alpha=0.294, solver=svd, tol=0.01;, score=0.808 total time=   0.0s
[CV 4/4] END .alpha=0.294, solver=svd, tol=0.01;, score=0.441 total time=   0.0s
[CV 1/4] END alpha=0.294, so

/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:216: LinAlgWarning: Ill-conditioned matrix (rcond=1.90136e-18): result may not be accurate.
  return linalg.solve(A, Xy, assume_a="pos", overwrite_a=True).T


[CV 4/4] END alpha=0.287, solver=cholesky, tol=1e-05;, score=0.441 total time=   0.0s
[CV 1/4] END alpha=0.287, solver=cholesky, tol=1e-07;, score=0.852 total time=   0.0s
[CV 2/4] END alpha=0.287, solver=cholesky, tol=1e-07;, score=0.742 total time=   0.0s
[CV 3/4] END alpha=0.287, solver=cholesky, tol=1e-07;, score=0.808 total time=   0.0s
[CV 4/4] END alpha=0.287, solver=cholesky, tol=1e-07;, score=0.441 total time=   0.0s
[CV 1/4] END alpha=0.287, solver=cholesky, tol=0.01;, score=0.852 total time=   0.0s
[CV 2/4] END alpha=0.287, solver=cholesky, tol=0.01;, score=0.742 total time=   0.0s
[CV 3/4] END alpha=0.287, solver=cholesky, tol=0.01;, score=0.808 total time=   0.0s
[CV 4/4] END alpha=0.287, solver=cholesky, tol=0.01;, score=0.441 total time=   0.0s
[CV 1/4] END alpha=0.287, solver=lsqr, tol=1e-05;, score=0.852 total time=   0.0s
[CV 2/4] END alpha=0.287, solver=lsqr, tol=1e-05;, score=0.742 total time=   0.0s
[CV 3/4] END alpha=0.287, solver=lsqr, tol=1e-05;, score=0.808 tot

/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:349: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV 1/4] END alpha=13, solver=cholesky, tol=1e-07;, score=0.823 total time=   0.0s
[CV 2/4] END alpha=13, solver=cholesky, tol=1e-07;, score=0.711 total time=   0.0s
[CV 3/4] END alpha=13, solver=cholesky, tol=1e-07;, score=0.747 total time=   0.0s
[CV 4/4] END alpha=13, solver=cholesky, tol=1e-07;, score=0.700 total time=   0.0s
[CV 1/4] END alpha=13, solver=sparse_cg, tol=1e-05;, score=0.823 total time=   0.0s
[CV 2/4] END alpha=13, solver=sparse_cg, tol=1e-05;, score=0.711 total time=   0.0s
[CV 3/4] END alpha=13, solver=sparse_cg, tol=1e-05;, score=0.747 total time=   0.0s
[CV 4/4] END alpha=13, solver=sparse_cg, tol=1e-05;, score=0.700 total time=   0.0s
[CV 1/4] END alpha=13, solver=sparse_cg, tol=1e-07;, score=0.823 total time=   0.0s
[CV 2/4] END alpha=13, solver=sparse_cg, tol=1e-07;, score=0.711 total time=   0.0s
[CV 3/4] END alpha=13, solver=sparse_cg, tol=1e-07;, score=0.747 total time=   0.0s
[CV 4/4] END alpha=13, solver=sparse_cg, tol=1e-07;, score=0.700 total time=   0

### Kernel Ridge Regression

In [22]:
KernelRidge?

Init signature:
KernelRidge(
    alpha=1,
    *,
    kernel='linear',
    gamma=None,
    degree=3,
    coef0=1,
    kernel_params=None,
)
Docstring:     
Kernel ridge regression.

Kernel ridge regression (KRR) combines ridge regression (linear least
squares with l2-norm regularization) with the kernel trick. It thus
learns a linear function in the space induced by the respective kernel and
the data. For non-linear kernels, this corresponds to a non-linear
function in the original space.

The form of the model learned by KRR is identical to support vector
regression (SVR). However, different loss functions are used: KRR uses
squared error loss while support vector regression uses epsilon-insensitive
loss, both combined with l2 regularization. In contrast to SVR, fitting a
KRR model can be done in closed-form and is typically faster for
medium-sized datasets. On the other hand, the learned model is non-sparse
and thus slower than SVR, which learns a sparse model for epsilon > 0, at
pred

In [23]:
param_grid_rd = {"alpha": [x/100 for x in range(100)],
              "kernel": ['linear', 'poly', 'rbf', 'sigmoid', "chi2", "laplacian"],#, "exponential" 
              "degree": [1, 2, 3],
              "gamma": [x/10 for x in range(10)]}

In [24]:
n_hyper = np.prod([x for x in map(len, param_grid_rd.values())])

In [25]:
n_hyper

np.int64(18000)

In [26]:
%%time
model = KernelRidge()
model.fit(Xs, ys)
rd = RandomizedSearchCV(model, param_grid_rd, cv=4, error_score=-1000, n_jobs=-1, scoring="r2", verbose=4, n_iter=int(n_hyper*.25))
rd.fit(Xs, ys)
print("Best score: " + str(rd.best_score_))

Fitting 4 folds for each of 4500 candidates, totalling 18000 fits


/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model

[CV 3/4] END alpha=86, solver=cholesky, tol=1e-05;, score=0.584 total time=   0.0s
[CV 4/4] END alpha=86, solver=cholesky, tol=1e-05;, score=0.668 total time=   0.0s
[CV 1/4] END ..alpha=88, solver=auto, tol=1e-07;, score=0.674 total time=   0.0s
[CV 2/4] END ..alpha=88, solver=auto, tol=1e-07;, score=0.546 total time=   0.0s
[CV 3/4] END ..alpha=88, solver=auto, tol=1e-07;, score=0.580 total time=   0.0s
[CV 4/4] END ..alpha=88, solver=auto, tol=1e-07;, score=0.665 total time=   0.0s
[CV 1/4] END ...alpha=88, solver=auto, tol=0.01;, score=0.674 total time=   0.0s
[CV 2/4] END ...alpha=88, solver=auto, tol=0.01;, score=0.546 total time=   0.0s
[CV 3/4] END ...alpha=88, solver=auto, tol=0.01;, score=0.580 total time=   0.0s
[CV 4/4] END ...alpha=88, solver=auto, tol=0.01;, score=0.665 total time=   0.0s
[CV 1/4] END ...alpha=88, solver=svd, tol=1e-05;, score=0.674 total time=   0.0s
[CV 2/4] END ...alpha=88, solver=svd, tol=1e-05;, score=0.546 total time=   0.0s
[CV 3/4] END ...alpha=88

/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(


[CV 3/4] END ..alpha=95, solver=saga, tol=1e-07;, score=0.569 total time=   0.0s
[CV 4/4] END ..alpha=95, solver=saga, tol=1e-07;, score=0.656 total time=   0.0s
[CV 1/4] END ...alpha=95, solver=saga, tol=0.01;, score=0.662 total time=   0.0s
[CV 2/4] END ...alpha=95, solver=saga, tol=0.01;, score=0.535 total time=   0.0s
[CV 3/4] END ...alpha=95, solver=saga, tol=0.01;, score=0.569 total time=   0.0s
[CV 4/4] END ...alpha=95, solver=saga, tol=0.01;, score=0.657 total time=   0.0s
[CV 1/4] END ..alpha=96, solver=auto, tol=1e-05;, score=0.660 total time=   0.0s
[CV 2/4] END ..alpha=96, solver=auto, tol=1e-05;, score=0.534 total time=   0.0s
[CV 3/4] END ..alpha=96, solver=auto, tol=1e-05;, score=0.567 total time=   0.0s
[CV 4/4] END ..alpha=96, solver=auto, tol=1e-05;, score=0.655 total time=   0.0s
[CV 1/4] END alpha=98, solver=cholesky, tol=1e-07;, score=0.657 total time=   0.0s
[CV 2/4] END alpha=98, solver=cholesky, tol=1e-07;, score=0.531 total time=   0.0s
[CV 3/4] END alpha=98, s

...

[CV 2/4] END alpha=0.6, degree=2, gamma=0.1, kernel=poly;, score=0.782 total time=   0.1s
[CV 1/4] END alpha=0.72, degree=3, gamma=0.2, kernel=sigmoid;, score=-1.470 total time=   0.3s
[CV 3/4] END alpha=0.36, degree=3, gamma=0.3, kernel=chi2;, score=0.859 total time=   0.4s
[CV 1/4] END alpha=0.48, degree=2, gamma=0.9, kernel=sigmoid;, score=-0.128 total time=   1.4s
[CV 4/4] END alpha=0.33, degree=1, gamma=0.8, kernel=poly;, score=0.454 total time=   0.1s
[CV 3/4] END alpha=0.02, degree=3, gamma=0.0, kernel=poly;, score=-0.006 total time=   0.1s
[CV 2/4] END alpha=0.96, degree=2, gamma=0.5, kernel=sigmoid;, score=0.284 total time=   1.0s
[CV 1/4] END alpha=0.25, degree=2, gamma=0.3, kernel=rbf;, score=0.894 total time=   0.1s
[CV 2/4] END alpha=0.25, degree=2, gamma=0.3, kernel=rbf;, score=0.823 total time=   0.1s
[CV 3/4] END alpha=0.25, degree=2, gamma=0.3, kernel=rbf;, score=0.867 total time=   0.1s
[CV 1/4] END alpha=0.45, degree=3, gamma=0.4, kernel=chi2;, score=0.866 total time

/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model

[CV 2/4] END alpha=0.4, degree=3, gamma=0.9, kernel=chi2;, score=0.562 total time=   0.2s
[CV 3/4] END alpha=0.25, degree=2, gamma=0.4, kernel=poly;, score=0.871 total time=   0.1s
[CV 4/4] END alpha=0.5, degree=2, gamma=0.8, kernel=chi2;, score=0.730 total time=   0.4s
[CV 4/4] END alpha=0.93, degree=1, gamma=0.3, kernel=poly;, score=0.600 total time=   0.1s
[CV 4/4] END alpha=0.23, degree=1, gamma=0.8, kernel=sigmoid;, score=-0.169 total time=   1.7s
[CV 1/4] END alpha=0.18, degree=3, gamma=0.3, kernel=poly;, score=0.913 total time=   0.2s
[CV 2/4] END alpha=0.96, degree=1, gamma=0.4, kernel=sigmoid;, score=0.107 total time=   1.7s
[CV 1/4] END alpha=0.99, degree=1, gamma=0.6, kernel=laplacian;, score=0.722 total time=   0.1s
[CV 3/4] END alpha=0.53, degree=3, gamma=0.0, kernel=poly;, score=-0.006 total time=   0.1s
[CV 3/4] END alpha=0.72, degree=2, gamma=0.1, kernel=linear;, score=0.792 total time=   0.1s
[CV 2/4] END alpha=0.85, degree=3, gamma=0.2, kernel=linear;, score=0.746 tot

/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model/_ridge.py:255: UserWarning: Singular matrix in solving dual problem. Using least-squares solution instead.
  warnings.warn(
/home/pc1/.local/share/virtualenvs/clases-XAo6S3GO/lib/python3.10/site-packages/sklearn/linear_model

Best score: 0.8806585584699513
CPU times: user 57.6 s, sys: 7.23 s, total: 1min 4s
Wall time: 6min 50s


In [27]:
rd.best_score_

np.float64(0.8806585584699513)

In [28]:
rd.best_estimator_

KernelRidge(alpha=0.1, degree=1, gamma=0.1, kernel='laplacian')

### Test of the best model

In [ ]:
# To find the predicted y
r2_score(y_pred=mm_y.inverse_transform(rd.best_estimator_.predict(mm_x.transform(X_test))), y_true=y_test)

0.8205149894646999

In [33]:
#Sacamos el score
rd.best_estimator_.score((mm_x.transform(X_test)), mm_y.transform(y_test))

0.8205149894647